In [32]:
import torch
from torchtext.datasets import AG_NEWS
train_iter = iter(AG_NEWS(split='train'))

In [33]:
next(train_iter)

(3,
 "Wall St. Bears Claw Back Into the Black (Reuters) Reuters - Short-sellers, Wall Street's dwindling\\band of ultra-cynics, are seeing green again.")

In [34]:
next(train_iter)

(3,
 'Carlyle Looks Toward Commercial Aerospace (Reuters) Reuters - Private investment firm Carlyle Group,\\which has a reputation for making well-timed and occasionally\\controversial plays in the defense industry, has quietly placed\\its bets on another part of the market.')

In [35]:
next(train_iter)

(3,
 "Oil and Economy Cloud Stocks' Outlook (Reuters) Reuters - Soaring crude prices plus worries\\about the economy and the outlook for earnings are expected to\\hang over the stock market next week during the depth of the\\summer doldrums.")

### Prepare data processing pipeline

In [36]:
from torchtext.data.utils import get_tokenizer
from torchtext.vocab import build_vocab_from_iterator

In [37]:
tokenizer = get_tokenizer('basic_english')
train_iter = AG_NEWS(split='train')

In [38]:
def yield_tokens(data_iter):
    for _, text in data_iter:
        yield tokenizer(text)

In [39]:
vocab = build_vocab_from_iterator(yield_tokens(train_iter), specials=["<unk>"])
vocab.set_default_index(vocab["<unk>"])

In [40]:
vocab(['here', 'is', 'an', 'example'])

[475, 21, 30, 5297]

Prepare the text processing pipeline with the tokenizer and vocabulary. The text and label pipelines will be used to process the raw data strings from the dataset iterators.

In [41]:
text_pipeline = lambda x: vocab(tokenizer(x))
label_pipeline = lambda x: int(x) - 1

The text pipeline converts a text string into a list of integers based on the lookup table defined in the vocabulary. The label pipeline converts the label into integers. For example,

In [42]:
text_pipeline('here is the an example')

[475, 21, 2, 30, 5297]

In [43]:
label_pipeline('10')

9

### Generate data batch and iterator

In [44]:
from torch.utils.data import DataLoader
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

def collate_batch(batch):
    label_list, text_list, offsets = [], [], [0]
    for (_label, _text) in batch:
        label_list.append(label_pipeline(_label))
        processed_text = torch.tensor(text_pipeline(_text), dtype=torch.int64)
        text_list.append(processed_text)
        offsets.append(processed_text.size(0))

    label_list = torch.tensor(label_list, dtype=torch.int64)
    offsets = torch.tensor(offsets[:-1]).cumsum(dim=0)
    text_list = torch.cat(text_list)
    return label_list.to(device), text_list.to(device), offsets.to(device)

### Define Model

In [45]:
from torch import nn

In [46]:
class TextClassificationModel(nn.Module):
    def __init__(self, vocab_size, embed_dim, num_class):
        super().__init__()
        self.embedding = nn.EmbeddingBag(vocab_size, embed_dim, sparse=False)
        self.fc = nn.Linear(embed_dim, num_class)
        self.init_weights()

    def init_weights(self):
        initrange = 0.5
        self.embedding.weight.data.uniform_(-initrange, initrange)
        self.fc.weight.data.uniform_(-initrange, initrange)
        self.fc.bias.data.zero_()

    def forward(self, text, offsets):
        embedded = self.embedding(text, offsets)
        return self.fc(embedded)

In [47]:
train_iter = AG_NEWS(split='train')
num_class = len(set([label for (label, text) in train_iter]))
vocab_size = len(vocab)
emsize = 64
model = TextClassificationModel(vocab_size, emsize, num_class).to(device)

### Define functions to train the model and evaluate results

In [48]:
import time

def train(dataloader, criterion, optimizer, epoch):
    model.train()
    total_acc, total_count = 0, 0
    log_interval = 500
    start_time = time.time()

    for idx, (label, text, offsets) in enumerate(dataloader):
        print(f'text shape: {text.size()}')
        print(f'text : {text}')
        print(f'label shape: {label.size()}')
        print(f'label: {label}')
        
        optimizer.zero_grad()
        predicted_label = model(text, offsets)
        loss = criterion(predicted_label, label)
        loss.backward()
        torch.nn.utils.clip_grad_norm_(model.parameters(), 0.1)
        optimizer.step()
        total_acc += (predicted_label.argmax(1) == label).sum().item()
        total_count += label.size(0)
        if idx % log_interval == 0 and idx > 0:
            elapsed = time.time() - start_time
            print('| epoch {:3d} | {:5d}/{:5d} batches '
                  '| accuracy {:8.3f}'.format(epoch, idx, len(dataloader),
                                              total_acc/total_count))
            total_acc, total_count = 0, 0
            start_time = time.time()

def evaluate(dataloader, criterion):
    model.eval()
    total_acc, total_count = 0, 0

    with torch.no_grad():
        for idx, (label, text, offsets) in enumerate(dataloader):
            predicted_label = model(text, offsets)
            loss = criterion(predicted_label, label)
            total_acc += (predicted_label.argmax(1) == label).sum().item()
            total_count += label.size(0)
    return total_acc/total_count

### Split the dataset and run the model

In [49]:
from torch.utils.data.dataset import random_split
from torchtext.data.functional import to_map_style_dataset

In [50]:
EPOCHS = 10
LR = 5
BATCH_SIZE = 64

In [51]:
criterion = torch.nn.CrossEntropyLoss()
optimizer = torch.optim.SGD(model.parameters(), lr=LR)
scheduler = torch.optim.lr_scheduler.StepLR(optimizer, 1.0, gamma=0.1)
total_accu = None
train_iter, test_iter = AG_NEWS()
train_dataset = to_map_style_dataset(train_iter)
test_dataset = to_map_style_dataset(test_iter)
num_train = int(len(train_dataset) * 0.95)

split_train_, split_valid_ = \
    random_split(train_dataset, [num_train, len(train_dataset) - num_train])

train_dataloader = DataLoader(split_train_, batch_size=BATCH_SIZE,
                              shuffle=True, collate_fn=collate_batch)
valid_dataloader = DataLoader(split_valid_, batch_size=BATCH_SIZE,
                              shuffle=True, collate_fn=collate_batch)
test_dataloader = DataLoader(test_dataset, batch_size=BATCH_SIZE,
                             shuffle=True, collate_fn=collate_batch)

for epoch in range(1, EPOCHS + 1):
    epoch_start_time = time.time()
    train(train_dataloader, criterion, optimizer, epoch)
    accu_val = evaluate(valid_dataloader, criterion)
    if total_accu is not None and total_accu > accu_val:
      scheduler.step()
    else:
       total_accu = accu_val
    print('-' * 59)
    print('| end of epoch {:3d} | time: {:5.2f}s | '
          'valid accuracy {:8.3f} '.format(epoch,
                                           time.time() - epoch_start_time,
                                           accu_val))
    print('-' * 59)

text shape: torch.Size([2827])
text : tensor([ 2283,  4369,     1,  ...,     3,   345, 34223])
label shape: torch.Size([64])
label: tensor([0, 1, 2, 2, 1, 0, 0, 1, 2, 3, 2, 3, 1, 1, 1, 3, 3, 2, 2, 2, 0, 1, 1, 0,
        0, 1, 2, 1, 0, 3, 1, 1, 0, 0, 0, 1, 3, 3, 3, 3, 0, 3, 1, 3, 2, 3, 0, 0,
        0, 1, 3, 3, 1, 3, 2, 2, 1, 2, 0, 0, 3, 2, 1, 0])
text shape: torch.Size([2722])
text : tensor([1095,    3,   19,  ...,   26,   57,    1])
label shape: torch.Size([64])
label: tensor([0, 2, 2, 0, 1, 0, 0, 0, 3, 1, 0, 2, 1, 3, 2, 2, 1, 0, 1, 0, 0, 2, 0, 3,
        1, 1, 3, 2, 3, 1, 1, 2, 0, 0, 2, 1, 1, 1, 3, 3, 0, 3, 1, 1, 0, 2, 3, 1,
        3, 1, 3, 2, 0, 3, 1, 1, 3, 0, 1, 0, 0, 3, 2, 2])
text shape: torch.Size([2933])
text : tensor([10483,  1957,  2897,  ...,     5,   225,     1])
label shape: torch.Size([64])
label: tensor([2, 1, 2, 0, 2, 2, 2, 1, 3, 3, 2, 2, 3, 1, 3, 0, 3, 1, 1, 3, 3, 3, 2, 3,
        2, 2, 3, 3, 0, 1, 1, 0, 2, 3, 1, 0, 2, 2, 2, 1, 3, 2, 3, 0, 2, 0, 3, 2,
        1, 3, 3,

### Evaluate the model with test dataset

In [52]:
print('Checking the results of test dataset')
accu_test = evaluate(test_dataloader, criterion)
print(f'Test accuracy: {accu_test:8.3f}')

Checking the results of test dataset
Test accuracy:    0.907
